In [1]:
#Import Necessary Packages
import numpy as np
import pandas as pd
import nltk
from nltk.corpus import stopwords
import matplotlib.pyplot as plt
import textblob
from textblob import TextBlob
import seaborn as sn
import tensorflow
import keras
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.models import Sequential,Model
from tensorflow.keras.layers import Dense,Flatten,Embedding
from keras.layers.convolutional import Conv1D
from keras.layers.convolutional import MaxPooling1D
from collections import Counter
%matplotlib inline
import warnings
warnings.simplefilter('ignore')

In [8]:
# load doc into memory
def load_doc(filename):
    
    # open the file as read only
    file=open(filename,'r')
    text=file.read()
    #textcorrected=textblob.correct()
    file.close()
    return text

In [9]:
filename=r"F:\SimpliLearn NLP3\txt_sentoken\pos\cv000_29590.txt"
doc=load_doc(filename)
doc

'films adapted from comic books have had plenty of success , whether they\'re about superheroes ( batman , superman , spawn ) , or geared toward kids ( casper ) or the arthouse crowd ( ghost world ) , but there\'s never really been a comic book like from hell before . \nfor starters , it was created by alan moore ( and eddie campbell ) , who brought the medium to a whole new level in the mid \'80s with a 12-part series called the watchmen . \nto say moore and campbell thoroughly researched the subject of jack the ripper would be like saying michael jackson is starting to look a little odd . \nthe book ( or " graphic novel , " if you will ) is over 500 pages long and includes nearly 30 more that consist of nothing but footnotes . \nin other words , don\'t dismiss this film because of its source . \nif you can get past the whole comic book thing , you might find another stumbling block in from hell\'s directors , albert and allen hughes . \ngetting the hughes brothers to direct this seem

In [10]:
import re
import string
import os
STOPWORDS=set(stopwords.words('english'))

 
# turn a doc into clean tokens
def clean_doc(doc):
    tokens=doc.split() # split into tokens by white space
    table=str.maketrans('','',string.punctuation) # remove punctuation from each token
    tokens=[w.translate(table) for w in tokens]
    tokens=[re.sub(r'\([^)]*\)','',w) for w in tokens]
    tokens=[w for w in tokens if w.isalpha()] # remove remaining tokens that are not alphabetic
    tokens=[w for w in tokens if w not in STOPWORDS] # filter out stop words
    tokens=[w for w in tokens if len(w)>1] # filter out short tokens
    return tokens

In [11]:
# load doc and add to vocab
def add_doc_to_vocab(filename,vocab):
    doc=load_doc(filename)
    tokens=clean_doc(doc)
    vocab.update(tokens)  # update counts

In [12]:
# load all docs in a directory
def process_docs(directory,vocab,is_train):
    for filename in os.listdir(directory):
        if is_train and filename.startswith('cv9'):
            continue
        if not is_train and not filename.startswith('cv9'):
            continue
        path=directory+'/'+filename
        add_doc_to_vocab(path,vocab)

In [13]:
# define vocab
vocab=Counter()
process_docs(r"F:\SimpliLearn NLP3\txt_sentoken\neg",vocab,True)
process_docs(r"F:\SimpliLearn NLP3\txt_sentoken\pos",vocab,True)

print(len(vocab))

44276


In [14]:
print(vocab.most_common(50))

[('film', 7983), ('one', 4946), ('movie', 4826), ('like', 3201), ('even', 2262), ('good', 2080), ('time', 2041), ('story', 1907), ('films', 1873), ('would', 1844), ('much', 1824), ('also', 1757), ('characters', 1735), ('get', 1724), ('character', 1703), ('two', 1643), ('first', 1588), ('see', 1557), ('way', 1515), ('well', 1511), ('make', 1418), ('really', 1407), ('little', 1351), ('life', 1334), ('plot', 1288), ('people', 1269), ('bad', 1248), ('could', 1248), ('scene', 1241), ('movies', 1238), ('never', 1201), ('best', 1179), ('new', 1140), ('scenes', 1135), ('man', 1131), ('many', 1130), ('doesnt', 1118), ('know', 1092), ('dont', 1086), ('hes', 1024), ('great', 1014), ('another', 992), ('action', 985), ('love', 977), ('us', 967), ('go', 952), ('director', 948), ('end', 946), ('something', 945), ('still', 936)]


In [15]:
def save_list(lines,filename):
    data='\n'.join(lines)
    file=open(filename,'w')
    file.write(data)
    file.close()

In [16]:
min_occ=2
tokens=[i for (i,c) in vocab.items() if c>=min_occ]
print(len(tokens))

25767


In [17]:
# save tokens to a vocabulary file
save_list(tokens,'vocab.txt')

In [18]:
filename='vocab.txt'

In [19]:
# load doc into memory
def load_doc(filename):
    file=open(filename,'r')
    text=file.read()
    file.close()
    return text

In [20]:
# load the vocabulary
doc=load_doc(filename)
doc

'plot\ntwo\nteen\ncouples\ngo\nchurch\nparty\ndrink\ndrive\nget\naccident\none\nguys\ndies\ngirlfriend\ncontinues\nsee\nlife\nnightmares\nwhats\ndeal\nwatch\nmovie\nsorta\nfind\ncritique\nmindfuck\ngeneration\ntouches\ncool\nidea\npresents\nbad\npackage\nmakes\nreview\neven\nharder\nwrite\nsince\ngenerally\napplaud\nfilms\nattempt\nbreak\nmold\nmess\nhead\nlost\nhighway\nmemento\ngood\nways\nmaking\ntypes\nfolks\ndidnt\nsnag\ncorrectly\nseem\ntaken\npretty\nneat\nconcept\nexecuted\nterribly\nproblems\nwell\nmain\nproblem\nsimply\njumbled\nstarts\nnormal\ndownshifts\nfantasy\nworld\naudience\nmember\ngoing\ndreams\ncharacters\ncoming\nback\ndead\nothers\nlook\nlike\nstrange\napparitions\ndisappearances\nchase\nscenes\ntons\nweird\nthings\nhappen\nexplained\npersonally\ndont\nmind\ntrying\nunravel\nfilm\nevery\ngive\nclue\nkind\nfed\nbiggest\nobviously\ngot\nbig\nsecret\nhide\nseems\nwant\ncompletely\nfinal\nfive\nminutes\nmake\nentertaining\nthrilling\nengaging\nmeantime\nreally\nsad\np

In [21]:
# turn a doc into clean tokens
def clean_doc(doc,vocab):
    tokens=doc.split()
    table=str.maketrans('','',string.punctuation) # remove punctuation from each token
    tokens=[w.translate(table) for w in tokens]
    tokens=[w for w in tokens if w in vocab]  # filter out tokens not in vocab
    tokens=' '.join(tokens)
    return tokens

In [22]:
# load all docs in a directory
def process_docs(directory,vocab,is_train):
    documents=list()
    # walk through all files in the folder
    for filename in os.listdir(directory):
        if is_train and filename.startswith('cv9'):
            continue
        if not is_train and not filename.startswith('cv9'):
            continue
        # create the full path of the file to open
        path=directory+'/'+filename
        doc=load_doc(path)
        tokens=clean_doc(doc,vocab)
        documents.append(tokens)
    return documents

In [23]:
# load all training reviews
positive_docs=process_docs(r"F:\SimpliLearn NLP3\txt_sentoken\pos",vocab,True)
negative_docs=process_docs(r"F:\SimpliLearn NLP3\txt_sentoken\neg",vocab,True)

train_docs=negative_docs+positive_docs
train_docs

['plot two teen couples go church party drink drive get accident one guys dies girlfriend continues see life nightmares whats deal watch movie sorta find critique mindfuck movie teen generation touches cool idea presents bad package makes review even harder one write since generally applaud films attempt break mold mess head lost highway memento good bad ways making types films folks didnt snag one correctly seem taken pretty neat concept executed terribly problems movie well main problem simply jumbled starts normal downshifts fantasy world audience member idea whats going dreams characters coming back dead others look like dead strange apparitions disappearances looooot chase scenes tons weird things happen simply explained personally dont mind trying unravel film every give clue get kind fed films biggest problem obviously got big secret hide seems want hide completely final five minutes make things entertaining thrilling even engaging meantime really sad part arrow dig flicks like 

In [25]:
# create the tokenizer
tokenizer=Tokenizer()
tokenizer.fit_on_texts(train_docs) # fit the tokenizer on the documents

In [26]:
# sequence encode
encoded_docs=tokenizer.texts_to_sequences(train_docs)

In [27]:
# pad sequences
max_length=max([len(l.split()) for l in train_docs])
trainX=pad_sequences(encoded_docs,maxlen=max_length,truncating='post')

In [28]:
# define training labels
trainY=np.array([0 for _ in range(900)]+[1 for _ in range(900)])
trainY.shape

(1800,)

In [29]:
trainX.shape

(1800, 1380)

In [30]:
# load all test reviews
negative_docs=process_docs(r"F:\SimpliLearn NLP3\IMDB RATINGS\txt_sentoken\neg",vocab,False)
positive_docs=process_docs(r"F:\SimpliLearn NLP3\IMDB RATINGS\txt_sentoken\pos",vocab,False)

test_docs=negative_docs+positive_docs
test_docs

['may critic alive harbors much affection shlock monster movies delighted entertainment ron underwoods yarn tremors even last years yarn anaconda something films causes lower inhibitions return saturday afternoons youth spent company creature black lagoon blob deep rising yarn doesnt quite pass test sure enough modern monster movie ingredients place conspicuously collection bait excuse characters isolated location derelict cruise ship south china sea comic relief least one big explosion elements like sleazy shipping magnate anthony heald also appears doctorate marine biology slinky international jewel thief famke janssen whose white cotton tank top hides heart gold happens deep rising noteworthy primarily mechanical manner spits ingredients terrorist crew led mercenary hanover wes studi piloted boat captain finnegan treat williams shows loot cruise ship sea monsters show eat mercenary crew survivors make closing credits go lights hard work much enthusiasm sort joyless filmmaking especi

In [31]:
encoded_test_docs=tokenizer.texts_to_sequences(test_docs)
encoded_test_docs

[[75,
  2191,
  1011,
  13131,
  11,
  3103,
  27888,
  1203,
  30,
  13128,
  556,
  2574,
  30454,
  9671,
  10612,
  5,
  80,
  58,
  9671,
  4152,
  49,
  9,
  2060,
  4706,
  18849,
  590,
  2350,
  20622,
  2360,
  855,
  686,
  1398,
  179,
  18425,
  10651,
  396,
  1607,
  9671,
  37,
  117,
  1178,
  1647,
  177,
  64,
  852,
  1203,
  3,
  3452,
  127,
  16666,
  2243,
  8773,
  1668,
  13,
  3785,
  2503,
  14939,
  1733,
  467,
  1708,
  2246,
  1860,
  250,
  1382,
  108,
  2,
  61,
  3678,
  462,
  4,
  2959,
  17398,
  20487,
  1835,
  13049,
  12,
  435,
  28050,
  6293,
  36449,
  12813,
  1918,
  6357,
  2772,
  4550,
  5623,
  201,
  390,
  6961,
  5805,
  371,
  5234,
  416,
  1687,
  417,
  396,
  1607,
  5259,
  3055,
  4650,
  1046,
  10455,
  3452,
  2533,
  545,
  1050,
  6481,
  28720,
  2274,
  8868,
  37757,
  1561,
  1320,
  14900,
  1769,
  523,
  203,
  13526,
  1733,
  467,
  1860,
  2817,
  106,
  2025,
  6481,
  545,
  2733,
  21,
  2732,
  608,
  46,

In [39]:
testX=pad_sequences(encoded_test_docs,maxlen=max_length,padding='post')
testY=np.array([0 for _ in range(100)]+[1 for _ in range(100)])

In [40]:
testY.shape

(200,)

In [41]:
testX.shape

(200, 1380)

In [43]:
# define vocabulary size (largest integer value)
vocab_size=len(tokenizer.word_index)+1
vocab_size

44277

In [46]:
# define model
model=Sequential()
model.add(Embedding(vocab_size,100,input_length=max_length))
model.add(Conv1D(32,kernel_size=8,activation='relu'))
model.add(MaxPooling1D(pool_size=2))
model.add(Flatten())
model.add(Dense(10,activation='relu'))
model.add(Dense(1,activation='sigmoid'))

In [47]:
print(model.summary())

Model: "sequential_1"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 embedding_1 (Embedding)     (None, 1380, 100)         4427700   
                                                                 
 conv1d_1 (Conv1D)           (None, 1373, 32)          25632     
                                                                 
 max_pooling1d_1 (MaxPooling  (None, 686, 32)          0         
 1D)                                                             
                                                                 
 flatten (Flatten)           (None, 21952)             0         
                                                                 
 dense (Dense)               (None, 10)                219530    
                                                                 
 dense_1 (Dense)             (None, 1)                 11        
                                                      

In [48]:
# compile network
model.compile(loss='binary_crossentropy',optimizer='Adam',metrics=['accuracy'])

In [49]:
#fit the network
H=model.fit(trainX,trainY,epochs=10,verbose=2)

Epoch 1/10
Please report this to the TensorFlow team. When filing the bug, set the verbosity to 10 (on Linux, `export AUTOGRAPH_VERBOSITY=10`) and attach the full output.
Cause: 'arguments' object has no attribute 'posonlyargs'
To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert
Please report this to the TensorFlow team. When filing the bug, set the verbosity to 10 (on Linux, `export AUTOGRAPH_VERBOSITY=10`) and attach the full output.
Cause: 'arguments' object has no attribute 'posonlyargs'
To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert
57/57 - 12s - loss: 0.6917 - accuracy: 0.5261 - 12s/epoch - 216ms/step
Epoch 2/10
57/57 - 11s - loss: 0.5245 - accuracy: 0.7606 - 11s/epoch - 195ms/step
Epoch 3/10
57/57 - 14s - loss: 0.0652 - accuracy: 0.9911 - 14s/epoch - 241ms/step
Epoch 4/10
57/57 - 16s - loss: 0.0058 - accuracy: 0.9989 - 16s/epoch - 273ms/step
Epoch 5/10
57/57 - 14s - loss: 0.0026 - accuracy: 

In [50]:
#Evaluate
loss,acc=model.evaluate(testX,testY,verbose=0)
print('Test Accuracy:', acc*100)

Please report this to the TensorFlow team. When filing the bug, set the verbosity to 10 (on Linux, `export AUTOGRAPH_VERBOSITY=10`) and attach the full output.
Cause: 'arguments' object has no attribute 'posonlyargs'
To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert
Please report this to the TensorFlow team. When filing the bug, set the verbosity to 10 (on Linux, `export AUTOGRAPH_VERBOSITY=10`) and attach the full output.
Cause: 'arguments' object has no attribute 'posonlyargs'
To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert
Test Accuracy: 50.0


# Multichannel convolutional Layer

In [2]:
def load_doc(filename):
    file=open(filename,'r')
    text=file.read()
    file.close()
    return text

In [3]:
filename=r"F:\SimpliLearn NLP3\txt_sentoken\pos\cv000_29590.txt"
doc=load_doc(filename)
doc

'films adapted from comic books have had plenty of success , whether they\'re about superheroes ( batman , superman , spawn ) , or geared toward kids ( casper ) or the arthouse crowd ( ghost world ) , but there\'s never really been a comic book like from hell before . \nfor starters , it was created by alan moore ( and eddie campbell ) , who brought the medium to a whole new level in the mid \'80s with a 12-part series called the watchmen . \nto say moore and campbell thoroughly researched the subject of jack the ripper would be like saying michael jackson is starting to look a little odd . \nthe book ( or " graphic novel , " if you will ) is over 500 pages long and includes nearly 30 more that consist of nothing but footnotes . \nin other words , don\'t dismiss this film because of its source . \nif you can get past the whole comic book thing , you might find another stumbling block in from hell\'s directors , albert and allen hughes . \ngetting the hughes brothers to direct this seem

In [4]:

import re
import string
from nltk.corpus import stopwords
STOPWORDS=set(stopwords.words('english'))
def clean_doc(doc):
    tokens=doc.split()
    table=str.maketrans('','',string.punctuation)
    tokens=[w.translate(table) for w in tokens]
    tokens=[re.sub(r'\([^)]*\)','',w) for w in tokens]
    tokens=[w for w in tokens if w.isalpha()]
    tokens=[w for w in tokens if w not in STOPWORDS]
    tokens=[w for w in tokens if len(w)>1]
    return tokens
    

In [5]:
tokens=clean_doc(doc)
tokens

['films',
 'adapted',
 'comic',
 'books',
 'plenty',
 'success',
 'whether',
 'theyre',
 'superheroes',
 'batman',
 'superman',
 'spawn',
 'geared',
 'toward',
 'kids',
 'casper',
 'arthouse',
 'crowd',
 'ghost',
 'world',
 'theres',
 'never',
 'really',
 'comic',
 'book',
 'like',
 'hell',
 'starters',
 'created',
 'alan',
 'moore',
 'eddie',
 'campbell',
 'brought',
 'medium',
 'whole',
 'new',
 'level',
 'mid',
 'series',
 'called',
 'watchmen',
 'say',
 'moore',
 'campbell',
 'thoroughly',
 'researched',
 'subject',
 'jack',
 'ripper',
 'would',
 'like',
 'saying',
 'michael',
 'jackson',
 'starting',
 'look',
 'little',
 'odd',
 'book',
 'graphic',
 'novel',
 'pages',
 'long',
 'includes',
 'nearly',
 'consist',
 'nothing',
 'footnotes',
 'words',
 'dont',
 'dismiss',
 'film',
 'source',
 'get',
 'past',
 'whole',
 'comic',
 'book',
 'thing',
 'might',
 'find',
 'another',
 'stumbling',
 'block',
 'hells',
 'directors',
 'albert',
 'allen',
 'hughes',
 'getting',
 'hughes',
 'brot

In [6]:
def add_doc_to_vocab(filename,vocab):
    doc=load_doc(filename)
    tokens=clean_doc(doc)
    vocab.update(tokens)

In [7]:
import os
def process_docs(directory,vocab,is_train):
    for filename in os.listdir(directory):
        if is_train and filename.startswith('cv9'):
            continue
        if not is_train and not filename.startswith('cv9'):
            continue
        path=directory+'/'+filename
        add_doc_to_vocab(path,vocab)

In [8]:
from collections import Counter
vocab=Counter()

process_docs(r"F:\SimpliLearn NLP3\IMDB RATINGS\txt_sentoken\neg",vocab,True)
process_docs(r"F:\SimpliLearn NLP3\IMDB RATINGS\txt_sentoken\pos",vocab,True)

In [9]:
print(len(vocab))

44274


In [10]:
print(vocab.most_common(50))

[('film', 7975), ('one', 4939), ('movie', 4821), ('like', 3199), ('even', 2262), ('good', 2078), ('time', 2040), ('story', 1907), ('films', 1871), ('would', 1843), ('much', 1824), ('also', 1757), ('characters', 1734), ('get', 1724), ('character', 1700), ('two', 1641), ('first', 1588), ('see', 1557), ('way', 1514), ('well', 1510), ('make', 1415), ('really', 1407), ('little', 1350), ('life', 1334), ('plot', 1288), ('people', 1269), ('bad', 1247), ('could', 1247), ('scene', 1238), ('movies', 1237), ('never', 1201), ('best', 1179), ('new', 1139), ('scenes', 1134), ('man', 1130), ('many', 1130), ('doesnt', 1117), ('know', 1091), ('dont', 1086), ('hes', 1024), ('great', 1013), ('another', 990), ('action', 977), ('love', 977), ('us', 966), ('go', 952), ('director', 946), ('something', 945), ('end', 941), ('still', 935)]


In [11]:
min_occ=2
tokens=[k for k,c in vocab.items() if c>=min_occ]

In [12]:
print(len(tokens))

25763


In [13]:
def save_list(lines,filename):
    data='\n'.join(lines)
    file=open(filename,'w')
    file.write(data)
    file.close()

In [14]:
save_list(tokens,'vocab.txt')

In [15]:
def load_doc(filename):
    file=open(filename,'r')
    text=file.read()
    file.close()
    return text

In [16]:
doc=load_doc('vocab.txt')
doc

'plot\ntwo\nteen\ncouples\ngo\nchurch\nparty\ndrink\ndrive\nget\naccident\none\nguys\ndies\ngirlfriend\ncontinues\nsee\nlife\nnightmares\nwhats\ndeal\nwatch\nmovie\nsorta\nfind\ncritique\nmindfuck\ngeneration\ntouches\ncool\nidea\npresents\nbad\npackage\nmakes\nreview\neven\nharder\nwrite\nsince\ngenerally\napplaud\nfilms\nattempt\nbreak\nmold\nmess\nhead\nlost\nhighway\nmemento\ngood\nways\nmaking\ntypes\nfolks\ndidnt\nsnag\ncorrectly\nseem\ntaken\npretty\nneat\nconcept\nexecuted\nterribly\nproblems\nwell\nmain\nproblem\nsimply\njumbled\nstarts\nnormal\ndownshifts\nfantasy\nworld\naudience\nmember\ngoing\ndreams\ncharacters\ncoming\nback\ndead\nothers\nlook\nlike\nstrange\napparitions\ndisappearances\nchase\nscenes\ntons\nweird\nthings\nhappen\nexplained\npersonally\ndont\nmind\ntrying\nunravel\nfilm\nevery\ngive\nclue\nkind\nfed\nbiggest\nobviously\ngot\nbig\nsecret\nhide\nseems\nwant\ncompletely\nfinal\nfive\nminutes\nmake\nentertaining\nthrilling\nengaging\nmeantime\nreally\nsad\np

In [17]:
def clean_doc(doc,vocab):
    tokens=doc.split()
    table=str.maketrans('','',string.punctuation)
    tokens=[w.translate(table) for w in tokens]
    tokens=[w for w in tokens if w in vocab]
    tokens=' '.join(tokens)
    return tokens

In [18]:
def process_docs(directory,vocab,is_train):
    documents=list()
    for filename in os.listdir(directory):
        if is_train and filename.startswith('cv9'):
            continue
        if not is_train and not filename.startswith('cv9'):
            continue
        path=directory+'/'+filename
        doc=load_doc(path)
        tokens=clean_doc(doc,vocab)
        documents.append(tokens)
    return documents
    

In [19]:
negative_docs=process_docs(r"F:\SimpliLearn NLP3\IMDB RATINGS\txt_sentoken\neg",vocab,True)
positive_docs=process_docs(r"F:\SimpliLearn NLP3\IMDB RATINGS\txt_sentoken\pos",vocab,True)

In [20]:
import pickle
from pickle import dump,load

def save_dataset(dataset,filename):
    dump(dataset,open(filename,'wb'))
    print('Saved:%s'%filename)

In [21]:
trainX=negative_docs+positive_docs
trainY=np.array([0 for _ in range(900)]+[1 for _ in range(900)])
save_dataset([trainX,trainY],'train.pkl')

Saved:train.pkl


In [22]:
negative_docs=process_docs(r"F:\SimpliLearn NLP3\IMDB RATINGS\txt_sentoken\neg",vocab,False)
positive_docs=process_docs(r"F:\SimpliLearn NLP3\IMDB RATINGS\txt_sentoken\pos",vocab,False)

testX=negative_docs+positive_docs
testY=np.array([0 for _ in range(100)]+[1 for _ in range(100)])
save_dataset([testX,testY],'test.pkl')

Saved:test.pkl


In [23]:
def load_dataset(filename):
    return load(open(filename,'rb'))

In [24]:
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences

In [25]:
def create_tokenizer(lines):
    tokenizer=Tokenizer()
    tokenizer.fit_on_texts(lines)
    return tokenizer

In [26]:
def max_length(lines):
    return max([len(l.split()) for l in lines])

In [27]:
#vocab_size=len(tokenizer.word_index)+1

In [28]:
def encode_text(tokenizer,lines,length):
    encoded=tokenizer.texts_to_sequences(lines)
    padded=pad_sequences(encoded,maxlen=length,padding='post')
    return padded

In [29]:
from tensorflow.keras.models import Model,Sequential
from tensorflow.keras.layers import Dropout,Flatten,Input,BatchNormalization,Dense,Embedding
from keras.layers.convolutional import Conv1D,MaxPooling1D
from keras.layers.merge import concatenate

We will define a model with three input channels for processing 4-grams, 6-grams, and 8-grams of movie review text.

Each channel is comprised of the following elements:

Input layer that defines the length of input sequences.
Embedding layer set to the size of the vocabulary and 100-dimensional real-valued representations.
One-dimensional convolutional layer with 32 filters and a kernel size set to the number of words to read at once.
Max Pooling layer to consolidate the output from the convolutional layer.
Flatten layer to reduce the three-dimensional output to two dimensional for concatenation.

In [30]:
#Define The Model
def create_model(length,vocab_size):
    # channel 1
    inputs1=Input(shape=(length,))
    embedding1=Embedding(vocab_size,100)(inputs1)
    conv1=Conv1D(32,kernel_size=4,activation='relu')(embedding1)
    drop1=Dropout(0.5)(conv1)
    pool1=MaxPooling1D(pool_size=2)(drop1)
    flat1=Flatten()(pool1)
    # channel 2
    inputs2=Input(shape=(length,))
    embedding2=Embedding(vocab_size,100)(inputs2)
    conv2=Conv1D(32,kernel_size=6,activation='relu')(embedding2)
    drop2=Dropout(0.5)(conv2)
    pool2=MaxPooling1D(pool_size=2)(drop2)
    flat2=Flatten()(pool2)
    
    # channel 3
    inputs3=Input(shape=(length,))
    embedding3=Embedding(vocab_size,100)(inputs3)
    conv3=Conv1D(32,kernel_size=8,activation='relu')(embedding3)
    drop3=Dropout(0.5)(conv3)
    pool3=MaxPooling1D(pool_size=2)(drop3)
    flat3=Flatten()(pool3)
    # merge
    merged=concatenate([flat1,flat2,flat3])
    # interpretation
    dense1=Dense(10,activation='relu')(merged)
    outputs=Dense(1,activation='sigmoid')(dense1)
    model=Model(inputs=[inputs1,inputs2,inputs3],outputs=outputs)
    # compile
    model.compile(optimizer='adam',loss='binary_crossentropy',metrics=['accuracy'])
    # summarize
    print(model.summary())
    return model
    
    

A multi-channel convolutional neural network for document classification involves using multiple versions of the standard model with different sized kernels. This allows the document to be processed at different resolutions or different n-grams (groups of words) at a time, whilst the model learns how to best integrate these interpretations.

In [31]:
trainLines,trainLabels=load_dataset('train.pkl')

tokenizer=create_tokenizer(trainLines)
length=max_length(trainLines)

vocab_size=len(tokenizer.word_index)+1

trainX=encode_text(tokenizer,trainLines,length)

In [32]:
trainX.shape

(1800, 1380)

In [33]:
model=create_model(length,vocab_size)
print(model.summary())

Model: "model"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 input_1 (InputLayer)           [(None, 1380)]       0           []                               
                                                                                                  
 input_2 (InputLayer)           [(None, 1380)]       0           []                               
                                                                                                  
 input_3 (InputLayer)           [(None, 1380)]       0           []                               
                                                                                                  
 embedding (Embedding)          (None, 1380, 100)    4427500     ['input_1[0][0]']                
                                                                                              

In [34]:
H=model.fit([trainX,trainX,trainX],np.array(trainLabels),epochs=10,batch_size=16)

Epoch 1/10
Please report this to the TensorFlow team. When filing the bug, set the verbosity to 10 (on Linux, `export AUTOGRAPH_VERBOSITY=10`) and attach the full output.
Cause: 'arguments' object has no attribute 'posonlyargs'
To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert
Please report this to the TensorFlow team. When filing the bug, set the verbosity to 10 (on Linux, `export AUTOGRAPH_VERBOSITY=10`) and attach the full output.
Cause: 'arguments' object has no attribute 'posonlyargs'
To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert
113/113 [==============================] - 53s 460ms/step - loss: 0.6891 - accuracy: 0.5378
Epoch 2/10
113/113 [==============================] - 48s 428ms/step - loss: 0.4848 - accuracy: 0.7778
Epoch 3/10
113/113 [==============================] - 53s 467ms/step - loss: 0.0656 - accuracy: 0.9800
Epoch 4/10
113/113 [==============================] - 53s 474ms/step 

In [35]:
model.save('convolutionaltext.h5')

In [36]:
from tensorflow.keras.models import load_model

In [37]:
testLines,testLabels=load_dataset('test.pkl')

In [38]:
trainX=encode_text(tokenizer,trainLines,length)
testX=encode_text(tokenizer,testLines,length)

In [39]:
print(trainX.shape,testX.shape)

(1800, 1380) (200, 1380)


In [40]:
model=load_model('convolutionaltext.h5')

In [42]:
loss,acc=model.evaluate([trainX,trainX,trainX],np.array(trainLabels),verbose=0)
print('Train Accuracy: %f'%(acc*100))

loss,acc=model.evaluate([testX,testX,testX],np.array(testLabels),verbose=0)
print('Test Accuracy: %f'% (acc*100))

Train Accuracy: 100.000000
Test Accuracy: 82.499999
